In [1]:
import os
os.environ['PIP_CACHE_DIR'] = '/scratch/ola5/cache'
os.environ['HF_HOME'] = '/scratch/ola5/cache'

%cd Open-Sora-Plan

/scratch/ola5/opensora/Open-Sora-Plan


/scratch/ola5/opensora/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [2]:
import torch

device = "cuda" if torch.cuda.is_available() else "cpu"
weight_dtype = torch.bfloat16

from opensora.models.causalvideovae import ae_stride_config, ae_channel_config, ae_norm, ae_denorm, CausalVAEModelWrapper
import imageio

/scratch/ola5/opensora/lib/python3.10/site-packages/torchvision/transforms/_functional_video.py:6: UserWarning: The 'torchvision.transforms._functional_video' module is deprecated since 0.12 and will be removed in the future. Please use the 'torchvision.transforms.functional' module instead.
  warnings.warn(
/scratch/ola5/opensora/lib/python3.10/site-packages/torchvision/transforms/_transforms_video.py:22: UserWarning: The 'torchvision.transforms._transforms_video' module is deprecated since 0.12 and will be removed in the future. Please use the 'torchvision.transforms' module instead.
  warnings.warn(


[2024-08-13 01:01:57,414] [INFO] [real_accelerator.py:203:get_accelerator] Setting ds_accelerator to cuda (auto detect)
 [WARNING]  async_io requires the dev libaio .so object and headers but these were not found.
 [WARNING]  async_io: please install the libaio-dev package with apt
 [WARNING]  If libaio is already installed (perhaps from source), try setting the CFLAGS and LDFLAGS environment variables to where it can be found.
 [WARNING]  Please specify the CUTLASS repo directory as environment variable $CUTLASS_PATH


/usr/bin/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status


 [WARNING]  sparse_attn requires a torch version >= 1.5 and < 2.0 but detected 2.1
 [WARNING]  using untested triton version (2.1.0), only 1.0.0 is known to be compatible


/scratch/ola5/opensora/lib/python3.10/site-packages/torchvision/transforms/functional_tensor.py:5: UserWarning: The torchvision.transforms.functional_tensor module is deprecated in 0.15 and will be **removed in 0.17**. Please don't rely on it. You probably just need to use APIs in torchvision.transforms.functional or in torchvision.transforms.v2.functional.
  warnings.warn(


In [3]:
vae = CausalVAEModelWrapper("./models/vae")
vae.vae = vae.vae.to(device=device, dtype=weight_dtype)
if True:
    vae.vae.enable_tiling()
    vae.vae.tile_overlap_factor = 0.125
    vae.vae.tile_sample_min_size = 256
    vae.vae.tile_latent_min_size = 32
    vae.vae.tile_sample_min_size_t = 29
    vae.vae.tile_latent_min_size_t = 8
vae.vae_scale_factor = ae_stride_config['CausalVAEModel_D4_4x8x8']
vae.eval()
'''vae'''

/scratch/ola5/opensora/lib/python3.10/site-packages/diffusers/configuration_utils.py:245: FutureWarning: It is deprecated to pass a pretrained model name or path to `from_config`.If you were trying to load a model, please use <class 'opensora.models.causalvideovae.model.causal_vae.modeling_causalvae.CausalVAEModel'>.load_config(...) followed by <class 'opensora.models.causalvideovae.model.causal_vae.modeling_causalvae.CausalVAEModel'>.from_config(...) instead. Otherwise, please make sure to pass a configuration dictionary instead. This functionality will be removed in v1.0.0.
  deprecate("config-passed-as-path", "1.0.0", deprecation_message, standard_warn=False)
The config attributes {'decoder_spatial_upsample_unup': ['', '', '', ''], 'encoder_spatial_downsample_undown': ['', '', '', ''], 'in_channels': 3, 'loss_params': {'disc_start': 1, 'disc_weight': 0.5, 'kl_weight': 1e-06, 'logvar_init': 0.0}, 'loss_type': 'opensora.models.ae.videobase.losses.LPIPSWithDiscriminator', 'lr': 1e-05, 

init from ./models/vae/checkpoint.ckpt
Load from normal model!


'vae'

In [4]:
import pickle
with open('latents.pkl', 'rb') as f:
    latent = pickle.load(f)

with torch.no_grad():
    video = vae.decode(latent.to(vae.vae.dtype))
    video = ((video / 2.0 + 0.5).clamp(0, 1) * 255).to(dtype=torch.uint8).cpu().permute(0, 1, 3, 4, 2).contiguous()
    print(video.shape)

torch.Size([1, 93, 720, 1280, 3])


In [5]:
imageio.mimwrite("osp8.mp4", video[0], fps=24, quality=8)

In [6]:
from IPython.display import HTML
from base64 import b64encode

mp4 = open('/scratch/ola5/opensora/Open-Sora-Plan/osp8.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=1280 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)